### An engineering problem from "Engineering Optimization" by Xin-She Yang

Goal: Design an optimal spring (cheapest / least material needed) that does the job. Parameters we can change: $d$, the diameter of the coil; $L$, the length of the spring; $w$, the thickness of the wire.

Task: Minimize $$(2+L)dw^2$$ subject to the constraints
\begin{align*}
g_1(L,d,w) &= 1 - \frac{d^3L}{7178w^4} \leq 0\\[5pt]
g_2(L,d,w) &= \frac{4d^2 - wd}{12566dw^3 - w^4} + \frac{1}{5108w^2} - 1 \leq 0\\[5pt]
g_3(L,d,w) &= 1 - \frac{140.45w}{d^2L} \leq 0\\[5pt]
g_4(L,d,w) &= \frac{w+d}{1.5} - 1 \leq 0
\end{align*}
with boundary conditions
$$
0.05 \leq w \leq 2.0
\qquad\qquad
0.25 \leq d \leq 1.3
\qquad\qquad
2.0 \leq L \leq 15.0
$$

In [2]:
import math
import random

In [3]:
def random_in_range(lower, upper):
    return random.random() * (upper - lower) + lower
random_in_range(2, 15)

7.191027336174431

In [4]:
def g1(L,d,w):
    return 1 - d**3 * L / (7178 * w**4)

def g2(L,d,w):
    return (4*d**2 - w*d)/(12566 * d * w**3 - w**4) + 1/(5108*w**2) - 1

def g3(L,d,w):
    return 1 - 140.45 * w / (d**2*L)

def g4(L,d,w):
    return (w+d)/1.5 - 1

def satisfies_constraints(L,d,w):
    return g1(L,d,w) <= 0 and g2(L,d,w) <= 0 and g3(L,d,w) <= 0 and g4(L,d,w) <= 0

In [5]:
def score(L,d,w):  # w-squared is "w**2" not "w^2"
    return (2+L)*d*w**2

In [6]:
def tweak(L,d,w):
    delta_w = 0.01
    delta_d = 0.01
    delta_L = 0.1
    
    new_w = w + random_in_range(-1, 1) * delta_w
    while new_w < 0.05 or new_w > 2:
        new_w = w + random_in_range(-1, 1) * delta_w
    
    new_d = d + random_in_range(-1, 1) * delta_d
    while new_d < 0.25 or new_d > 1.3:
        new_d = d + random_in_range(-1, 1) * delta_d
        
    new_L = L + random_in_range(-1, 1) * delta_L
    while new_L < 2 or new_L > 15:
        new_L = L + random_in_range(-1, 1) * delta_L
        
    return (new_L, new_d, new_w)
        
tweak(15, 1.3, 2.0)

(14.937625225852454, 1.2947285994812368, 1.9943841844620613)

In [7]:
def random_solution():
    return (
        random_in_range(2, 15),
        random_in_range(0.25, 1.3),
        random_in_range(0.05, 2),
    )
print(random_solution())

(8.503440073556614, 1.215130153306415, 1.954922170217535)


In [8]:
# what does the * do
def test(num1, num2):
    return num1 + num2
L = [1,3]
test(*L)

4

In [9]:
def hill_climbing():
    
    start = random_solution()
    while not satisfies_constraints(*start):
        start = random_solution()
    sol = start
    value = score(*sol)

    bad = 0
    while True:
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)
        new_value = score(*new_sol)
        if new_value < value:
            bad = 0
            sol = new_sol
            value = new_value
            
        else:
            bad += 1
            if bad > 1000:
                print(value)
                return sol
    


In [10]:
sol = hill_climbing()
#sol = [2.02310938, 0.25113418, 0.05218225]
# L, d, w
print(sol)
print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))
print(score(*sol))

0.0068805520270037125
(9.006314472438776, 0.2500170690136024, 0.05000412741244301)
-2.1363839258361597 -0.31699706862769494 -11.475017697295582 -0.799985869049303
0.0068805520270037125


In [11]:
old_sol = [2.02310938, 0.25113418, 0.05218225]
score(*old_sol)

0.0027511436522230925

In [12]:
# smarter: sample 1000 tweaks to find a good initial_temp that gives a desired p_0
# or: heat the system slowly until the % of worsening solutions is what you want
initial_temp = 0.005
alpha = 0.99
final_temp = initial_temp / 1000
trials_per_temp = 10000

start = random_solution()
while not satisfies_constraints(*start):
    start = random_solution()
sol = start
value = score(*sol)

In [13]:
temp = initial_temp
generation = 0
best_sol = None
best_score = None

while temp >= final_temp:
    generation += 1
    accepted_worse = 0
    total_worse = 0
    for i in range(trials_per_temp):
        new_sol = tweak(*sol)
        while not satisfies_constraints(*new_sol):
            new_sol = tweak(*sol)

        new_value = score(*new_sol)
        
        delta = new_value - value
        delta *= -1
        if delta >= 0:
            sol = new_sol
            value = new_value
            if best_score is None or value < best_score:
                best_sol = sol
                best_score = value
        else:
            total_worse += 1
            p = math.exp(delta/temp)
            r = random.random()
            if r <= p:
                accepted_worse += 1
                sol = new_sol
                value = new_value

    print(
        f"Gen #{generation}: temp = {temp:.6f}, "
        f"best score = {best_score:.8f}, "
        f"cur score = {value:.8f}, "
        f"worse accepted = {round(accepted_worse/total_worse*100,2):.2f}%"
    )
    temp = temp * alpha
    


Gen #1: temp = 0.005000, best score = 0.00318075, cur score = 0.01317111, worse accepted = 75.36%
Gen #2: temp = 0.004950, best score = 0.00318075, cur score = 0.00921724, worse accepted = 59.21%
Gen #3: temp = 0.004901, best score = 0.00318075, cur score = 0.02757053, worse accepted = 67.20%
Gen #4: temp = 0.004851, best score = 0.00318075, cur score = 0.00899667, worse accepted = 58.91%
Gen #5: temp = 0.004803, best score = 0.00318075, cur score = 0.01563525, worse accepted = 66.60%
Gen #6: temp = 0.004755, best score = 0.00318075, cur score = 0.01675689, worse accepted = 56.82%
Gen #7: temp = 0.004707, best score = 0.00318075, cur score = 0.01009962, worse accepted = 62.72%
Gen #8: temp = 0.004660, best score = 0.00318075, cur score = 0.01604365, worse accepted = 56.95%
Gen #9: temp = 0.004614, best score = 0.00318075, cur score = 0.01475345, worse accepted = 59.69%
Gen #10: temp = 0.004568, best score = 0.00318075, cur score = 0.01538009, worse accepted = 58.17%
Gen #11: temp = 0.0

Gen #89: temp = 0.002065, best score = 0.00282661, cur score = 0.00603980, worse accepted = 53.17%
Gen #90: temp = 0.002044, best score = 0.00282661, cur score = 0.00844879, worse accepted = 62.13%
Gen #91: temp = 0.002024, best score = 0.00282661, cur score = 0.00556486, worse accepted = 61.04%
Gen #92: temp = 0.002003, best score = 0.00282661, cur score = 0.00787471, worse accepted = 55.16%
Gen #93: temp = 0.001983, best score = 0.00282661, cur score = 0.00559748, worse accepted = 61.35%
Gen #94: temp = 0.001964, best score = 0.00282661, cur score = 0.00613000, worse accepted = 64.03%
Gen #95: temp = 0.001944, best score = 0.00282661, cur score = 0.00674110, worse accepted = 61.36%
Gen #96: temp = 0.001924, best score = 0.00282661, cur score = 0.00672075, worse accepted = 49.03%
Gen #97: temp = 0.001905, best score = 0.00282661, cur score = 0.00433382, worse accepted = 59.39%
Gen #98: temp = 0.001886, best score = 0.00282661, cur score = 0.01129704, worse accepted = 60.69%
Gen #99: t

Gen #175: temp = 0.000870, best score = 0.00282661, cur score = 0.00589635, worse accepted = 48.49%
Gen #176: temp = 0.000861, best score = 0.00282661, cur score = 0.00529465, worse accepted = 47.93%
Gen #177: temp = 0.000853, best score = 0.00282661, cur score = 0.00539788, worse accepted = 40.05%
Gen #178: temp = 0.000844, best score = 0.00282661, cur score = 0.00583703, worse accepted = 45.23%
Gen #179: temp = 0.000836, best score = 0.00282661, cur score = 0.00512243, worse accepted = 43.47%
Gen #180: temp = 0.000827, best score = 0.00282661, cur score = 0.00613741, worse accepted = 48.94%
Gen #181: temp = 0.000819, best score = 0.00282661, cur score = 0.00489782, worse accepted = 49.51%
Gen #182: temp = 0.000811, best score = 0.00282661, cur score = 0.00475974, worse accepted = 44.58%
Gen #183: temp = 0.000803, best score = 0.00282661, cur score = 0.00439465, worse accepted = 47.84%
Gen #184: temp = 0.000795, best score = 0.00282661, cur score = 0.00370539, worse accepted = 52.32%


Gen #258: temp = 0.000378, best score = 0.00282661, cur score = 0.00537380, worse accepted = 33.86%
Gen #259: temp = 0.000374, best score = 0.00282661, cur score = 0.00483649, worse accepted = 31.56%
Gen #260: temp = 0.000370, best score = 0.00282661, cur score = 0.00547199, worse accepted = 35.61%
Gen #261: temp = 0.000367, best score = 0.00282661, cur score = 0.00375781, worse accepted = 37.87%
Gen #262: temp = 0.000363, best score = 0.00282661, cur score = 0.00375528, worse accepted = 33.96%
Gen #263: temp = 0.000359, best score = 0.00282661, cur score = 0.00366420, worse accepted = 37.88%
Gen #264: temp = 0.000356, best score = 0.00282661, cur score = 0.00329811, worse accepted = 35.76%
Gen #265: temp = 0.000352, best score = 0.00282661, cur score = 0.00450894, worse accepted = 40.62%
Gen #266: temp = 0.000349, best score = 0.00282661, cur score = 0.00353979, worse accepted = 40.30%
Gen #267: temp = 0.000345, best score = 0.00282661, cur score = 0.00330167, worse accepted = 37.46%


Gen #340: temp = 0.000166, best score = 0.00282661, cur score = 0.00334587, worse accepted = 31.53%
Gen #341: temp = 0.000164, best score = 0.00282661, cur score = 0.00333895, worse accepted = 27.55%
Gen #342: temp = 0.000162, best score = 0.00282661, cur score = 0.00383468, worse accepted = 29.54%
Gen #343: temp = 0.000161, best score = 0.00282661, cur score = 0.00300442, worse accepted = 30.38%
Gen #344: temp = 0.000159, best score = 0.00282661, cur score = 0.00328705, worse accepted = 30.25%
Gen #345: temp = 0.000158, best score = 0.00282661, cur score = 0.00329486, worse accepted = 29.54%
Gen #346: temp = 0.000156, best score = 0.00282661, cur score = 0.00326530, worse accepted = 26.99%
Gen #347: temp = 0.000154, best score = 0.00282661, cur score = 0.00359273, worse accepted = 29.73%
Gen #348: temp = 0.000153, best score = 0.00282661, cur score = 0.00309402, worse accepted = 31.04%
Gen #349: temp = 0.000151, best score = 0.00282661, cur score = 0.00357600, worse accepted = 32.28%


Gen #422: temp = 0.000073, best score = 0.00282555, cur score = 0.00291056, worse accepted = 21.32%
Gen #423: temp = 0.000072, best score = 0.00282555, cur score = 0.00295071, worse accepted = 20.85%
Gen #424: temp = 0.000071, best score = 0.00282555, cur score = 0.00296405, worse accepted = 22.03%
Gen #425: temp = 0.000071, best score = 0.00282555, cur score = 0.00300549, worse accepted = 20.72%
Gen #426: temp = 0.000070, best score = 0.00282555, cur score = 0.00302343, worse accepted = 21.10%
Gen #427: temp = 0.000069, best score = 0.00282555, cur score = 0.00302089, worse accepted = 21.37%
Gen #428: temp = 0.000068, best score = 0.00282555, cur score = 0.00332846, worse accepted = 21.18%
Gen #429: temp = 0.000068, best score = 0.00282555, cur score = 0.00292451, worse accepted = 20.85%
Gen #430: temp = 0.000067, best score = 0.00282555, cur score = 0.00305865, worse accepted = 21.47%
Gen #431: temp = 0.000066, best score = 0.00282555, cur score = 0.00304911, worse accepted = 19.60%


Gen #504: temp = 0.000032, best score = 0.00282352, cur score = 0.00301426, worse accepted = 8.89%
Gen #505: temp = 0.000032, best score = 0.00282352, cur score = 0.00293973, worse accepted = 8.46%
Gen #506: temp = 0.000031, best score = 0.00282352, cur score = 0.00284868, worse accepted = 9.16%
Gen #507: temp = 0.000031, best score = 0.00282352, cur score = 0.00298154, worse accepted = 8.11%
Gen #508: temp = 0.000031, best score = 0.00282352, cur score = 0.00292223, worse accepted = 9.14%
Gen #509: temp = 0.000030, best score = 0.00282352, cur score = 0.00290823, worse accepted = 8.20%
Gen #510: temp = 0.000030, best score = 0.00282352, cur score = 0.00292722, worse accepted = 8.79%
Gen #511: temp = 0.000030, best score = 0.00282352, cur score = 0.00296483, worse accepted = 8.35%
Gen #512: temp = 0.000029, best score = 0.00282352, cur score = 0.00289419, worse accepted = 7.84%
Gen #513: temp = 0.000029, best score = 0.00282352, cur score = 0.00302742, worse accepted = 8.68%
Gen #514: 

Gen #587: temp = 0.000014, best score = 0.00282213, cur score = 0.00285262, worse accepted = 2.12%
Gen #588: temp = 0.000014, best score = 0.00282213, cur score = 0.00286377, worse accepted = 2.28%
Gen #589: temp = 0.000014, best score = 0.00282213, cur score = 0.00284990, worse accepted = 2.23%
Gen #590: temp = 0.000013, best score = 0.00282213, cur score = 0.00286943, worse accepted = 2.00%
Gen #591: temp = 0.000013, best score = 0.00282213, cur score = 0.00283590, worse accepted = 1.65%
Gen #592: temp = 0.000013, best score = 0.00282213, cur score = 0.00285802, worse accepted = 2.55%
Gen #593: temp = 0.000013, best score = 0.00282213, cur score = 0.00285805, worse accepted = 1.66%
Gen #594: temp = 0.000013, best score = 0.00282213, cur score = 0.00286691, worse accepted = 2.09%
Gen #595: temp = 0.000013, best score = 0.00282213, cur score = 0.00285692, worse accepted = 1.88%
Gen #596: temp = 0.000013, best score = 0.00282213, cur score = 0.00287001, worse accepted = 1.62%
Gen #597: 

Gen #670: temp = 0.000006, best score = 0.00282213, cur score = 0.00284297, worse accepted = 0.25%
Gen #671: temp = 0.000006, best score = 0.00282213, cur score = 0.00283721, worse accepted = 0.35%
Gen #672: temp = 0.000006, best score = 0.00282213, cur score = 0.00282848, worse accepted = 0.31%
Gen #673: temp = 0.000006, best score = 0.00282213, cur score = 0.00283085, worse accepted = 0.20%
Gen #674: temp = 0.000006, best score = 0.00282213, cur score = 0.00283281, worse accepted = 0.31%
Gen #675: temp = 0.000006, best score = 0.00282213, cur score = 0.00284350, worse accepted = 0.27%
Gen #676: temp = 0.000006, best score = 0.00282213, cur score = 0.00283141, worse accepted = 0.21%
Gen #677: temp = 0.000006, best score = 0.00282213, cur score = 0.00283856, worse accepted = 0.29%
Gen #678: temp = 0.000006, best score = 0.00282213, cur score = 0.00283061, worse accepted = 0.34%
Gen #679: temp = 0.000005, best score = 0.00282213, cur score = 0.00283833, worse accepted = 0.28%
Gen #680: 

In [ ]:
best_sol

In [ ]:
sol = best_sol
print(g1(*sol), g2(*sol), g3(*sol), g4(*sol))

In [ ]:
score(*sol)